In [1]:
import pandas as pd
import json
import re

In [2]:
credits = pd.read_csv("input/credits.csv")


In [107]:
# Importing metadata csv to dataframe and dropping unneeded rows
metadata_dtype = {"adult": str,"overview": str, "budget": float, "id": int,"popularity": float, "video": str}

metadata = pd.read_csv("input/movies_metadata.csv", dtype=metadata_dtype)

metadata.drop_duplicates(subset=['id'], inplace=True)

metadata.drop(labels=["belongs_to_collection", "imdb_id", "homepage", "adult", "poster_path",
              "video", "tagline", "original_title"], inplace=True, axis=1, errors="ignore")

budget                                             genres      id  \
0      380000000.0  [{'id': 12, 'name': 'Adventure'}, {'id': 28, '...    1865   
1      300000000.0  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...     285   
2      280000000.0  [{'id': 28, 'name': 'Action'}, {'id': 12, 'nam...   99861   
3      270000000.0  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...    1452   
4      260000000.0  [{'id': 28, 'name': 'Action'}, {'id': 878, 'na...  335988   
...            ...                                                ...     ...   
45458          0.0                                                 []  335251   
45459          0.0                [{'id': 99, 'name': 'Documentary'}]  323132   
45460          0.0  [{'id': 28, 'name': 'Action'}, {'id': 53, 'nam...   82663   
45461          0.0  [{'id': 16, 'name': 'Animation'}, {'id': 878, ...  122662   
45462          0.0  [{'id': 10770, 'name': 'TV Movie'}, {'id': 28,...  249260   

      original_language                                           overview  \
0                    en  Captain Jack Sparrow crosses paths with a woma...   
1                    en  Captain Barbossa, long believed to be dead, ha...   
2                    en  When Tony Stark tries to jumpstart a dormant p...   
3                    en  Superman returns to discover his 5-year absenc...   
4                    en  Autobots and Decepticons are at war, with huma...   
...                 ...                                                ...   
45458                en  An exploration of the musical and social origi...   
45459                en  This film records a 12 day ritual performed by...   
45460                en  British soldiers force a recently captured IRA...   
45461                ja         Third film of the Mardock Scramble series.   
45462                en  A group of skiers are terrorized during spring...   

       popularity                               production_companies  \
0       27.887720  [{'name': 'Walt Disney Pictures', 'id': 2}, {'...   
1       31.363664  [{'name': 'Walt Disney Pictures', 'id': 2}, {'...   
2       37.379420  [{'name': 'Marvel Studios', 'id': 420}, {'name...   
3       13.284712  [{'name': 'DC Comics', 'id': 429}, {'name': 'L...   
4       39.186819  [{'name': 'Paramount Pictures', 'id': 4}, {'na...   
...           ...                                                ...   
45458    0.000000                                                 []   
45459    0.000000                                                 []   
45460         NaN                                                NaN   
45461         NaN                                                NaN   
45462         NaN                                                NaN   

                                    production_countries release_date  \
0      [{'iso_3166_1': 'US', 'name': 'United States o...   14/05/2011   
1      [{'iso_3166_1': 'US', 'name': 'United States o...   19/05/2007   
2      [{'iso_3166_1': 'US', 'name': 'United States o...   22/04/2015   
3      [{'iso_3166_1': 'US', 'name': 'United States o...   28/06/2006   
4      [{'iso_3166_1': 'US', 'name': 'United States o...   21/06/2017   
...                                                  ...          ...   
45458                                                 []          NaN   
45459                                                 []    1/01/1976   
45460                                                NaN          NaN   
45461                                                NaN          NaN   
45462                                                NaN          NaN   

            revenue  runtime  \
0      1.045714e+09    136.0   
1      9.610000e+08    169.0   
2      1.405404e+09    141.0   
3      3.910812e+08    154.0   
4      6.049421e+08    149.0   
...             ...      ...   
45458  0.000000e+00      0.0   
45459  0.000000e+00     45.0   
45460           NaN      NaN   
45461           NaN      NaN   
45462   

In [32]:
metadata = metadata[metadata['production_countries'].map(lambda x: type(x) == str and x!="[]" and x.startswith('[{') and x.endswith('}]') and len(x)<500)]
metadata = metadata[metadata['production_companies'].map(lambda x: type(x) == str and x!="[]" and x.startswith('[{') and x.endswith('}]') and len(x)<500)]
metadata = metadata[metadata['budget'].map(lambda x: x>0)]
metadata = metadata[metadata['runtime'].map(lambda x: x>0)]

li = metadata["production_countries"].map(lambda x: x.count(","))
b = li[li.map(lambda x: x < 2)]
b

0       1
1       1
2       1
3       1
4       1
       ..
8876    1
8878    1
8884    1
8888    1
8889    1
Name: production_countries, Length: 6045, dtype: int64

In [5]:
# Creating sub dataframes


In [6]:
# Expanding json genres to id, genre rows
genres = metadata.filter(['id', 'genres'], axis=1)

genres['json'] = [json.loads(x.replace("\'", "\"")) for x in genres['genres']]
genres['genre'] = [[genre['name'] for genre in row] for row in genres['json']]
genres.drop(labels=['json', 'genres'],inplace=True, axis=1)
genres = genres.explode('genre')

In [ ]:
countries = metadata.filter(['id', 'production_countries'], axis=1)
def rep(m):
    return m.group(0).replace("\"", "\'")

   
countries['json'] = [json.loads(re.sub("\w\"\w", rep, x.replace("\'", "\""))) for x in countries['production_countries']]
countries['production_country'] = [row for row in countries['json']]
countries = countries.explode('production_country')
countries['name'] = [row["name"] for row in countries['production_country']]
countries['iso_3166_1'] = [row['iso_3166_1'] for row in countries['production_country']]
countries.drop(labels=['json','production_countries', 'production_country'],inplace=True, axis=1)

countries

In [74]:
language = metadata.filter(['id', 'spoken_languages'], axis=1)

language['json'] = [json.loads(x.replace("\\", "\\\/").replace("\'", "\"")) for x in language['spoken_languages']]

language['language'] = [[language['iso_639_1'] for language in row] for row in language['json']]
language.drop(labels=['json', 'spoken_languages'],inplace=True, axis=1)
language = language.explode('language')
language

id language
0       1865       en
0       1865       es
1        285       en
2      99861       en
3       1452       en
...      ...      ...
8879  267931       en
8884  188529       ru
8884  188529       en
8888   51281       ru
8889  405050       en

[11626 rows x 2 columns]

In [106]:
companies = metadata.filter(['id', 'production_companies'], axis=1)
def rep2(m):
    return m.group(0).replace("\'", "\"")

companies['json'] = [json.loads(re.sub(".\'\: \'|{\'.|[\'\"], \'|.\'\:", rep2, x.replace("\"", "\'"))) for x in companies['production_companies']]
companies['name'] = [[x["name"] for x in row] for row in companies['json']]
companies = companies.explode('name')
companies.drop(labels=['json','production_companies'],inplace=True, axis=1)

companies

id                          name
0       1865          Walt Disney Pictures
0       1865       Jerry Bruckheimer Films
0       1865  Moving Picture Company (MPC)
1        285          Walt Disney Pictures
1        285       Jerry Bruckheimer Films
...      ...                           ...
8879  267931    Small Red Star Productions
8879  267931                  Artigo Indie
8884  188529              E1 Entertainment
8888   51281                 Stayer Studio
8889  405050                  Kmunications

[21701 rows x 2 columns]

[{"id": 931, "name": "jealousy'}, {"id": 4290, "name": "toy'}, {"id": 5202, "name": "boy'}, {"id": 6054, "name": "friendship"}, {"id": 9713, "name": "friends"}, {"id": 9823, "name": "rivalry'}, {"id": 165503, "name": "boy next door"}, {"id": 170722, "name": "new toy'}, {"id": 187065, "name": "toy comes to life"}]
[{'id': 10090, 'name': 'board game'}, {'id': 10941, 'name': 'disappearance'}, {'id': 15101, 'name': "based on children's book"}, {'id': 33467, 'name': 'new home'}, {'id': 158086, 'name': 'recluse'}, {'id': 158091, 'name': 'giant insect'}]
[{'id': 1495, 'name': 'fishing'}, {'id': 12392, 'name': 'best friend'}, {'id': 179431, 'name': 'duringcreditsstinger'}, {'id': 208510, 'name': 'old men'}]
[{'id': 818, 'name': 'based on novel'}, {'id': 10131, 'name': 'interracial relationship'}, {'id': 14768, 'name': 'single mother'}, {'id': 15160, 'name': 'divorce'}, {'id': 33455, 'name': 'chick flick'}]
[{"id": 1009, "name": "baby'}, {"id": 1599, "name": "midlife crisis"}, {"id": 2246, "nam

[{"id": 90, "name": "paris"}, {"id": 128, "name": "love triangle"}, {"id": 293, "name": "female nudity'}, {"id": 437, "name": "painter"}, {"id": 1326, "name": "infidelity'}, {"id": 2483, "name": "nudity'}, {"id": 9094, "name": "womanizer"}, {"id": 11869, "name": "mistress"}, {"id": 13149, "name": "pregnancy'}, {"id": 14669, "name": "older man younger woman relationship"}, {"id": 155794, "name": "physical abuse"}, {"id": 208710, "name": "picasso"}]
[{'id': 1946, 'name': 'restaurant'}, {'id': 9673, 'name': 'love'}, {'id': 10183, 'name': 'independent film'}, {'id': 11590, 'name': 'italian american'}, {'id': 155231, 'name': 'reference to william shakespeare'}]
[{"id": 212, "name": "london england"}, {"id": 237, "name": "gay'}, {"id": 1862, "name": "coming out"}, {"id": 10180, "name": "homosexuality'}, {"id": 13088, "name": "summer"}, {"id": 33458, "name": "gay man"}, {"id": 158718, "name": "lgbt"}, {"id": 187056, "name": "woman director"}]
[{"id": 409, "name": "africa"}, {"id": 2043, "name

[{"id": 388, "name": "scotland"}, {"id": 5698, "name": "egg"}, {"id": 11254, "name": "loss of virginity'}, {"id": 15055, "name": "kissing"}, {"id": 187056, "name": "woman director"}, {"id": 209003, "name": "gentile"}]
[{"id": 2548, "name": "kleptomania"}, {"id": 3363, "name": "hypnosis"}, {"id": 178210, "name": "marital problem"}, {"id": 215579, "name": "hypnotherapy'}]
[{'id': 592, 'name': 'capitalism'}, {'id': 14737, 'name': 'economics'}, {'id': 156052, 'name': 'unemployment'}, {'id': 156338, 'name': 'corporate greed'}]
[{'id': 242, 'name': 'new york'}, {'id': 1388, 'name': 'cinema'}, {'id': 5571, 'name': 'great depression'}, {'id': 13072, 'name': 'falling in love'}, {'id': 162262, 'name': 'movie star'}, {'id': 184989, 'name': 'spectacle'}]
[{"id": 128, "name": "love triangle"}, {"id": 428, "name": "nurse"}, {"id": 1252, "name": "suicide attempt"}, {"id": 1465, "name": "loss of family'}, {"id": 2504, "name": "world war i"}, {"id": 3460, "name": "russian revolution 1917'}, {"id": 3691

[{'id': 1480, 'name': 'baseball'}, {'id': 1482, 'name': 'trainer'}, {'id': 3658, 'name': 'career'}, {'id': 3754, 'name': 'legend'}, {'id': 4613, 'name': 'training'}, {'id': 6075, 'name': 'sport'}]
[{'id': 3190, 'name': 'menage a trois'}]
[{'id': 187056, 'name': 'woman director'}]
[{"id": 635, "name": "disc jockey'}, {"id": 3412, "name": "star"}, {"id": 5608, "name": "affection"}, {"id": 5626, "name": "from rags to riches"}, {"id": 12617, "name": "airplane crash"}, {"id": 156306, "name": "price of fame"}, {"id": 156783, "name": "blizzard"}]
[{'id': 2389, 'name': 'virgin'}, {'id': 3133, 'name': 'vampire'}, {'id': 4375, 'name': 'transformation'}, {'id': 4769, 'name': 'supernatural powers'}, {'id': 10327, 'name': 'undead'}, {'id': 10712, 'name': 'night club'}, {'id': 11441, 'name': 'lifting person in air'}, {'id': 12564, 'name': 'werewolf'}, {'id': 157499, 'name': 'mother son relationship'}]
[{"id": 9673, "name": "love"}, {"id": 10909, "name": "lawyer"}, {"id": 11937, "name": "conservative

[{"id": 255, "name": "male nudity'}, {"id": 1605, "name": "new love"}, {"id": 1808, "name": "lover (female)'}, {"id": 2038, "name": "love of one's life"}, {"id": 3691, "name": "forbidden love"}, {"id": 4663, "name": "lovers"}, {"id": 7879, "name": "secret love"}, {"id": 9986, "name": "crush"}, {"id": 10614, "name": "tragedy'}, {"id": 155231, "name": "reference to william shakespeare"}]
[{'id': 194170, 'name': 'televison'}]
[{"id": 736, "name": "journalist"}, {"id": 924, "name": "italian"}, {"id": 1956, "name": "world war ii"}, {"id": 2349, "name": "german"}, {"id": 4515, "name": "northern africa"}, {"id": 4595, "name": "u.s. army'}, {"id": 6092, "name": "army'}, {"id": 11106, "name": "infantry'}, {"id": 12193, "name": "reporter"}]
[{'id': 1562, 'name': 'hostage'}, {'id': 5608, 'name': 'affection'}, {'id': 10084, 'name': 'rescue'}, {'id': 15162, 'name': 'dog'}, {'id': 157987, 'name': 'animal actor'}, {'id': 191591, 'name': 'benji'}]
[{'id': 414, 'name': 'hunter'}, {'id': 3593, 'name': '

...

[{'id': 187056, 'name': 'woman director'}]
[{"id": 1964, "name": "cave"}, {"id": 2483, "name": "nudity'}, {"id": 2804, "name": "exploitation"}, {"id": 9815, "name": "psychic power"}, {"id": 9951, "name": "alien"}, {"id": 10292, "name": "gore"}, {"id": 10473, "name": "contagion spread"}, {"id": 12405, "name": "outer space"}, {"id": 14819, "name": "violence"}, {"id": 156173, "name": "eye gouging"}, {"id": 158744, "name": "stock footage"}, {"id": 166109, "name": "child murder"}]
[{'id': 734, 'name': 'bullfight'}]
[{'id': 9882, 'name': 'space'}, {'id': 229550, 'name': 'hayabusa'}]
[{'id': 187056, 'name': 'woman director'}]
[{'id': 417, 'name': 'corruption'}, {'id': 180491, 'name': 'cycling'}, {'id': 224174, 'name': 'bike racing'}]
[{"id": 5565, "name": "biography'}, {"id": 6412, "name": "rhythm and blues"}, {"id": 10764, "name": "crack cocaine"}, {"id": 187056, "name": "woman director"}, {"id": 208640, "name": "lifetime"}]
[{'id': 741, 'name': 'transplantation'}, {'id': 2519, 'name': 'cana

[{'id': 8636, 'name': 'blood splatter'}, {'id': 9826, 'name': 'murder'}, {'id': 15167, 'name': 'police detective'}, {'id': 160313, 'name': 'forensic'}, {'id': 161982, 'name': 'murder investigation'}]
[{'id': 5657, 'name': 'australia'}, {'id': 9675, 'name': 'prequel'}, {'id': 15162, 'name': 'dog'}, {'id': 193760, 'name': 'australian outback'}, {'id': 236104, 'name': 'australian folklore'}]
[{'id': 223629, 'name': 'dragons'}]
[{"id": 187056, "name": "woman director"}, {"id": 192115, "name": "photgraphy'}]
[{'id': 18029, 'name': 'trapped'}, {'id': 161294, 'name': 'biologist'}]
[{'id': 9826, 'name': 'murder'}, {'id': 10909, 'name': 'lawyer'}, {'id': 11168, 'name': 'private investigator'}, {'id': 33519, 'name': 'courtroom'}]
[{'id': 187056, 'name': 'woman director'}]
[{'id': 703, 'name': 'detective'}, {'id': 33519, 'name': 'courtroom'}, {'id': 171183, 'name': 'flirting'}, {'id': 190901, 'name': 'perry mason'}]
[{'id': 190901, 'name': 'perry mason'}]
[{'id': 801, 'name': 'bounty hunter'}, {'

[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{'id': 6027, 'name': 'music'}, {'id': 9704, 'name': 'ventriloquist'}, {'id': 191410, 'name': 'ventriloquism'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id": 9716, "name": "stand-up comedy'}]
[{"id"

[{'id': 154802, 'name': 'silent film'}, {'id': 165556, 'name': 'barber shop'}]
[{'id': 2723, 'name': 'medium'}, {'id': 3358, 'name': 'haunted house'}]
[{'id': 207317, 'name': 'christmas'}]
[{"id": 591, "name": "cia"}, {"id": 11131, "name": "biohazard"}, {"id": 190904, "name": "mi5'}, {"id": 225136, "name": "bio terrorism"}, {"id": 232488, "name": "terrorism threat"}]
[{'id': 5096, 'name': 'natural disaster'}, {'id': 10084, 'name': 'rescue'}, {'id': 10617, 'name': 'disaster'}]
[{"id": 293, "name": "female nudity'}, {"id": 3205, "name": "fairy tale"}, {"id": 9937, "name": "suspense"}, {"id": 10224, "name": "haunting"}, {"id": 155440, "name": "hitchcockian"}, {"id": 198680, "name": "tuscany'}, {"id": 208611, "name": "1950s"}]
[{'id': 1442, 'name': 'winter'}, {'id': 1890, 'name': 'camping'}, {'id': 13130, 'name': 'teenager'}, {'id': 44451, 'name': 'lost'}]
[{'id': 818, 'name': 'based on novel'}, {'id': 8440, 'name': 'ex-cop'}, {'id': 9937, 'name': 'suspense'}, {'id': 11436, 'name': 'redemp

[{'id': 223629, 'name': 'dragons'}]
[{'id': 4344, 'name': 'musical'}]
[{'id': 2546, 'name': 'mask'}, {'id': 2598, 'name': 'museum'}, {'id': 2863, 'name': 'mannequin'}, {'id': 6158, 'name': 'cult'}, {'id': 6259, 'name': 'psychopath'}, {'id': 9713, 'name': 'friends'}, {'id': 9826, 'name': 'murder'}, {'id': 11221, 'name': 'blood'}, {'id': 12339, 'name': 'slasher'}, {'id': 13130, 'name': 'teenager'}, {'id': 15001, 'name': 'demon'}, {'id': 202723, 'name': 'powers'}, {'id': 203471, 'name': 'telekinetic'}, {'id': 203476, 'name': 'wax'}]
[{'id': 983, 'name': 'brazilian'}]
[{'id': 10107, 'name': 'sinbad'}]
[{'id': 187056, 'name': 'woman director'}]
[{"id": 6895, "name": "philippines"}, {"id": 40850, "name": "destiny'}, {"id": 215397, "name": "pinoy'}]
[{'id': 187056, 'name': 'woman director'}]
[{'id': 2673, 'name': 'horse'}, {'id': 3205, 'name': 'fairy tale'}, {'id': 11162, 'name': 'miniseries'}, {'id': 189099, 'name': 'giant'}]
[{"id": 13000, "name": "based on short film"}, {"id": 34094, "name

In [ ]:
metadata.to_csv('output/metadata_clean.csv', index=False)
genres.to_csv('output/genres.csv', index=False)
countries.to_csv('output/production_countries.csv', index=False)
companies.to_csv('output/production_companies.csv', index=False)
language.to_csv('output/spoken_languages.csv', index=False)
